(Loading can take a long time. Please be patient.)

In [1]:
# @title Installing Requirements
%%capture
!pip install gradio
# Installs Unsloth, Xformers (Flash Attention) and all other packages!
!pip install "unsloth[colab-new] @ git+https://github.com/unslothai/unsloth.git"

# We have to check which Torch version for Xformers (2.3 -> 0.0.27)
from torch import __version__; from packaging.version import Version as V
xformers = "xformers==0.0.27" if V(__version__) < V("2.4.0") else "xformers"
!pip install --no-deps {xformers} trl peft accelerate bitsandbytes triton

from unsloth import FastLanguageModel
import torch
max_seq_length = 2048 # Choose any! We auto support RoPE Scaling internally!
dtype = None # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True # Use 4bit quantization to reduce memory usage. Can be False.

# 4bit pre quantized models we support for 4x faster downloading + no OOMs.
fourbit_models = [
    #"unsloth/Meta-Llama-3.1-8B-bnb-4bit",      # Llama-3.1 15 trillion tokens model 2x faster!
    "Solshine/mergekit-passthrough-aogjzpb",
    #"unsloth/Meta-Llama-3.1-70B-bnb-4bit",
    #"unsloth/Meta-Llama-3.1-405B-bnb-4bit",    # We also uploaded 4bit for 405b!
    #"unsloth/Mistral-Nemo-Base-2407-bnb-4bit", # New Mistral 12b 2x faster!
    #"unsloth/Mistral-Nemo-Instruct-2407-bnb-4bit",
    #"unsloth/mistral-7b-v0.3-bnb-4bit",        # Mistral v3 2x faster!
    #"unsloth/mistral-7b-instruct-v0.3-bnb-4bit",
    #"unsloth/Phi-3.5-mini-instruct",           # Phi-3.5 2x faster!
    #"unsloth/Phi-3-medium-4k-instruct",
    #"unsloth/gemma-2-9b-bnb-4bit",
    #"unsloth/gemma-2-27b-bnb-4bit",            # Gemma 2x faster!
] # More models at https://huggingface.co/unsloth

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "Solshine/mergekit-passthrough-aogjzpb",
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
    token = "XXXXX", # use one if using gated models like meta-llama/Llama-2-7b-hf

)

alpaca_prompt = """Below is an instruction that describes a task. Reason through the query inside <thinking> tags, and then provide your final response inside <output> tags. If you detect that you made a mistake in your reasoning at any point, correct yourself inside <reflection> tags. Write a response that appropriately completes the request.

### Instruction:
{}

### Response:
{}"""

EOS_TOKEN = tokenizer.eos_token # Must add EOS_TOKEN
def formatting_prompts_func(examples):
    instructions = examples["prompt"]
    outputs = examples["response"]
    texts = []
    for instruction, output in zip(instructions, outputs):
        # Must add EOS_TOKEN, otherwise your generation will go on forever!
        text = alpaca_prompt.format(instruction, output) + EOS_TOKEN
        texts.append(text)
    return {"text": texts}

In [5]:
# Ensure model is prepared for inference
model = FastLanguageModel.for_inference(model)

In [ ]:
# @title Create Gradio User Inferface
import gradio as gr

MASTER_PROMPT = """You are an assistant who answers all questions by first thinking internally using thinking tags, then reflects on your thinking, then answers, and then reflects on your answer offering any needed corrections. You are concise and accurate."""

# Add this function for the chatbot
def chatbot(message, history):
    # Combine history and master prompt and new message
    full_prompt = MASTER_PROMPT + "\n\n" + "\n".join([f"Human: {h[0]}\nAI: {h[1]}" for h in history])
    full_prompt += f"\nHuman: {message}\nAI:"

    inputs = tokenizer([alpaca_prompt.format(full_prompt, "")], return_tensors="pt").to("cuda")

    output = model.generate(**inputs, max_new_tokens=1000, temperature=0.7)
    response = tokenizer.decode(output[0], skip_special_tokens=True)

    # Extract the AI's response
    ai_response = response.split("AI:")[-1].strip()

    return ai_response

# Create the Gradio interface
iface = gr.ChatInterface(
    chatbot,
    title="AI Assistant",
    description="Ask questions, get reflections.",
    theme="soft",
    examples=[
        "How do I make fertilizer for tomatoes in Oregon?",
        "What is Korean Natural Farming?",
        "Can you explain the philosophy behind quantum physics?",
        "Please explain quantum entanglement in simple terms.",
    ],
)

# Launch the interface
iface.launch(share=True, debug=True)


Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
Running on public URL: https://88a900ce9e5af38193.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
